# Predicting Product Ratings using Customer Reviews

In [0]:
# start the timer
import time
start_time = time.time()

## Environment Setup

**`Classroom-Setup`**

In [0]:
%run ./Includes/Classroom-Setup

### Loading the DataFrame

In [0]:
textDF = spark.read.csv("/mnt/training/reviews/reviews.csv", inferSchema = True, header=True, escape='"')
display(textDF.limit(1000))

Id ProductId UserId ProfileName HelpfulnessNumerator HelpfulnessDenominator Score Time Summary Text 1 B001E4KFG0 A3SGXH7AUHU8GW delmartian 1 1 5 1303862400 Good Quality Dog Food I have bought several of the Vitality canned dog food products and have found them all to be of good quality. The product looks more like a stew than a processed meat and it smells better. My Labrador is finicky and she appreciates this product better than most. 2 B00813GRG4 A1D87F6ZCVE5NK dll pa 0 0 1 1346976000 Not as Advertised Product arrived labeled as Jumbo Salted Peanuts...the peanuts were actually small sized unsalted. Not sure if this was an error or if the vendor intended to represent the product as "Jumbo". 3 B000LQOCH0 ABXLMWJIXXAIN Natalia Corres "Natalia Corres" 1 1 4 1219017600 "Delight" says it all This is a confection that has been around a few centuries. It is a light, pillowy citrus gelatin with nuts - in this case Filberts. And it is cut into tiny squares and then liberally coated with powdered sugar. And it is a tiny mouthful of heaven. Not too chewy, and very flavorful. I highly recommend this yummy treat. If you are familiar with the story of C.S. Lewis' "The Lion, The Witch, and The Wardrobe" - this is the treat that seduces Edmund into selling out his Brother and Sisters to the Witch. 4 B000UA0QIQ A395BORC6FGVXV Karl 3 3 2 1307923200 Cough Medicine If you are looking for the secret ingredient in Robitussin I believe I have found it. I got this in addition to the Root Beer Extract I ordered (which was good) and made some cherry soda. The flavor is very medicinal. 5 B006K2ZZ7K A1UQRSCLF8GW1T Michael D. Bigham "M. Wassir" 0 0 5 1350777600 Great taffy Great taffy at a great price. There was a wide assortment of yummy taffy. Delivery was very quick. If your a taffy lover, this is a deal. 6 B006K2ZZ7K ADT0SRK1MGOEU Twoapennything 0 0 4 1342051200 Nice Taffy I got a wild hair for taffy and ordered this five pound bag. The taffy was all very enjoyable with many flavors: watermelon, root beer, melon, peppermint, grape, etc. My only complaint is there was a bit too much red/black licorice-flavored pieces (just not my particular favorites). Between me, my kids, and my husband, this lasted only two weeks! I would recommend this brand of taffy -- it was a delightful treat. 7 B006K2ZZ7K A1SP2KVKFXXRU1 David C. Sullivan 0 0 5 1340150400 Great! Just as good as the expensive brands! This saltwater taffy had great flavors and was very soft and chewy. Each candy was individually wrapped well. None of the candies were stuck together, which did happen in the expensive version, Fralinger's. Would highly recommend this candy! I served it at a beach-themed party and everyone loved it! 8 B006K2ZZ7K A3JRGQVEQN31IQ Pamela G. Williams 0 0 5 1336003200 Wonderful, tasty taffy This taffy is so good. It is very soft and chewy. The flavors are amazing. I would definitely recommend you buying it. Very satisfying!! 9 B000E7L2R4 A1MZYO9TZK0BBI R. James 1 1 5 1322006400 Yay Barley Right now I'm mostly just sprouting this so my cats can eat the grass. They love it. I rotate it around with Wheatgrass and Rye too 10 B00171APVA A21BT40VZCCYT4 Carol A. Reed 0 0 5 1351209600 Healthy Dog Food This is a very healthy dog food. Good for their digestion. Also good for small puppies. My dog eats her required amount at every feeding. 11 B0001PB9FE A3HDKO7OW0QNK4 Canadian Fan 1 1 5 1107820800 The Best Hot Sauce in the World I don't know if it's the cactus or the tequila or just the unique combination of ingredients, but the flavour of this hot sauce makes it one of a kind! We picked up a bottle once on a trip we were on and brought it back home with us and were totally blown away! When we realized that we simply couldn't find it anywhere in our city we were bummed. Now, because of the magic of the internet, we have a case of the sauce and are ecstatic because of it. If you love hot sauce..I mean really love hot sauce, but don't want a sauce that tastelessly burns your throat, g

In [0]:
# check numbers of rows and columns

print((textDF.count(), len(textDF.columns)))

(568454, 10)


In [0]:
# sample 10% data for debugging
textDF = textDF.sample(False, 0.1)

### Selecting Columns

In [0]:
textDF = textDF.select("Id", "ProductId", "Score", "Summary", "Text")

textDF.cache().count()

Out[14]: 57119

In [0]:
textDF.printSchema()

root
 |-- Id: integer (nullable = true)
 |-- ProductId: string (nullable = true)
 |-- Score: integer (nullable = true)
 |-- Summary: string (nullable = true)
 |-- Text: string (nullable = true)



In [0]:
from pyspark.sql.types import IntegerType
from pyspark.sql.functions import col

textDF = textDF.withColumn('Score', col('Score').cast(IntegerType()))

In [0]:
textDF.printSchema()

root
 |-- Id: integer (nullable = true)
 |-- ProductId: string (nullable = true)
 |-- Score: integer (nullable = true)
 |-- Summary: string (nullable = true)
 |-- Text: string (nullable = true)



## LDA

In [0]:
import sparknlp

from sparknlp.annotator import *
from sparknlp.common import *
from sparknlp.base import *
from nltk.corpus import stopwords

from pyspark.ml import Pipeline


In [0]:
## text cleaning annotators & Sentiment Analysis stages
documentAssembler = DocumentAssembler()\
    .setInputCol("Text")\
    .setOutputCol("document")
    
senEmbedder = UniversalSentenceEncoder.pretrained(name="tfhub_use", lang="en")\
 .setInputCols(["document"])\
 .setOutputCol("sentence_embeddings")

sentimentModel = SentimentDLModel.pretrained(name='sentimentdl_use_twitter', lang="en")\
    .setInputCols(["sentence_embeddings"])\
    .setOutputCol("sentiment")

finisher = Finisher() \
    .setInputCols(["sentiment"]) \
    .setOutputCols(["sentiment_result2"]) \
    .setOutputAsArray(False) \
    .setCleanAnnotations(True)

from pyspark.ml.feature import StringIndexer

## string indexer on sentiment results 
sentIndex = StringIndexer(inputCol='sentiment_result2',outputCol='sent_label')

from pyspark.ml.feature import Tokenizer,StopWordsRemover, CountVectorizer,IDF,StringIndexer


## LDA pre precessing steps
tokenizer = Tokenizer(inputCol="Text", outputCol="token_text")
stopremove = StopWordsRemover(inputCol='token_text',outputCol='stop_tokens')
count_vec = CountVectorizer(inputCol='stop_tokens',outputCol='c_vec')


from pyspark.ml.clustering import LDA

# Trains a LDA model.
lda = LDA(k=10, maxIter=10, featuresCol='c_vec')

## assemble features vector
from pyspark.ml.feature import VectorAssembler
from pyspark.ml.linalg import Vector
assembler = VectorAssembler(inputCols=['sent_label','topicDistribution'],outputCol='features')

## create pipeline for sentiment analysis, lda, and vector assembler
from pyspark.ml import Pipeline


lda_pipe = Pipeline(stages=[documentAssembler, senEmbedder, sentimentModel, finisher, sentIndex, tokenizer, stopremove, count_vec, lda, assembler])


tfhub_use download started this may take some time.
Approximate size to download 923.7 MB
[OK!]
sentimentdl_use_twitter download started this may take some time.
Approximate size to download 11.4 MB
[OK!]


In [0]:
lda_model = lda_pipe.fit(textDF)
processed = lda_model.transform(textDF).persist()

In [0]:
display(processed)

Id ProductId Score Summary Text sentiment_result2 sent_label token_text stop_tokens c_vec topicDistribution features 5 B006K2ZZ7K 5 Great taffy Great taffy at a great price. There was a wide assortment of yummy taffy. Delivery was very quick. If your a taffy lover, this is a deal. positive 0.0 List(great, taffy, at, a, great, price., , there, was, a, wide, assortment, of, yummy, taffy., , delivery, was, very, quick., , if, your, a, taffy, lover,, this, is, a, deal.) List(great, taffy, great, price., , wide, assortment, yummy, taffy., , delivery, quick., , taffy, lover,, deal.) Map(vectorType -> sparse, length -> 138549, indices -> List(0, 5, 285, 698, 820, 1253, 2323, 2773, 3925, 4409, 5339, 19283), values -> List(3.0, 2.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 2.0, 1.0)) Map(vectorType -> dense, length -> 10, values -> List(0.005236686550598841, 0.005224697304993408, 0.00522621758721869, 0.005229692881361002, 0.005224523817218892, 0.005244311001291487, 0.005233420393775082, 0.005249792319068091, 0.9528979943942993, 0.005232663750175271)) Map(vectorType -> dense, length -> 11, values -> List(0.0, 0.005236686550598841, 0.005224697304993408, 0.00522621758721869, 0.005229692881361002, 0.005224523817218892, 0.005244311001291487, 0.005233420393775082, 0.005249792319068091, 0.9528979943942993, 0.005232663750175271)) 17 B001GVISJM 2 poor taste I love eating them and they are good for watching TV and looking at movies! It is not too sweet. I like to transfer them to a zip lock baggie so they stay fresh so I can take my time eating them. positive 0.0 List(i, love, eating, them, and, they, are, good, for, watching, tv, and, looking, at, movies!, it, is, not, too, sweet., i, like, to, transfer, them, to, a, zip, lock, baggie, so, they, stay, fresh, so, i, can, take, my, time, eating, them.) List(love, eating, good, watching, tv, looking, movies!, sweet., like, transfer, zip, lock, baggie, stay, fresh, take, time, eating, them.) Map(vectorType -> sparse, length -> 138549, indices -> List(2, 4, 7, 32, 74, 88, 119, 120, 156, 591, 728, 1455, 3469, 4306, 5026, 6266, 8137, 36291), values -> List(1.0, 1.0, 1.0, 1.0, 1.0, 2.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0)) Map(vectorType -> dense, length -> 10, values -> List(0.004448161108790056, 0.004437972971644085, 0.004439283652490741, 0.00444222746998604, 0.00443784311581882, 0.004454759506764526, 0.004445396661996366, 0.004459320533416299, 0.959990285193029, 0.004444749786064036)) Map(vectorType -> dense, length -> 11, values -> List(0.0, 0.004448161108790056, 0.004437972971644085, 0.004439283652490741, 0.00444222746998604, 0.00443784311581882, 0.004454759506764526, 0.004445396661996366, 0.004459320533416299, 0.959990285193029, 0.004444749786064036)) 23 B001GVISJM 5 Delicious product! I can remember buying this candy as a kid and the quality hasn't dropped in all these years. Still a superb product you won't be disappointed with. negative 1.0 List(i, can, remember, buying, this, candy, as, a, kid, and, the, quality, hasn't, dropped, in, all, these, years., still, a, superb, product, you, won't, be, disappointed, with.) List(remember, buying, candy, kid, quality, dropped, years., still, superb, product, disappointed, with.) Map(vectorType -> sparse, length -> 138549, indices -> List(10, 47, 97, 111, 268, 401, 531, 762, 1463, 1667, 2972, 3853), values -> List(1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0, 1.0)) Map(vectorType -> dense, length -> 10, values -> List(0.0068575941950072515, 0.006841856587054536, 0.0068438490610422354, 0.006848416651910043, 0.006841622393480426, 0.0068675501158173705, 0.0068532686488196395, 0.006874717043881701, 0.9383188176985096, 0.006852307604477306)) Map(vectorType -> dense, length -> 11, values -> List(1.0, 0.0068575941950072515, 0.006841856587054536, 0.0068438490610422354, 0.006848416651910043, 0.006841622393480426, 0.0068675501158173705, 0.0068532686488196395, 0.006874717043881701, 0.9383188176985096, 0.006852307604477306)) 26 B001

In [0]:
(training,testing) = processed.randomSplit([0.8,0.2], seed=100)

In [0]:
from pyspark.ml.classification import RandomForestClassifier
nb = RandomForestClassifier(numTrees=3, maxDepth=2, featuresCol='features', labelCol="Score", seed=100)
fitted = nb.fit(training)
amazon_prediction = fitted.transform(testing)

In [0]:
from pyspark.ml.evaluation import MulticlassClassificationEvaluator

evaluator = MulticlassClassificationEvaluator(labelCol="Score", predictionCol="prediction", metricName="accuracy")
accuracy = evaluator.evaluate(amazon_prediction)
print("Accuracy of model at predicting user rating was: {}".format(accuracy))

Accuracy of model at predicting user rating was: 0.6397602730710845